In [6]:
import time

start = time.perf_counter()
c=0
c+=1
end = time.perf_counter()
print(f"Time taken: {end-start:0.4f} seconds")

Time taken: 0.0001 seconds


In [1]:
import asyncio
import numpy as np

def background(f):
  def wrapped(*args, **kwargs):
    return asyncio.get_event_loop().run_in_executor(None, f, *args, **kwargs)
  return wrapped

@background
def f():
  c=0
  for j in range(100):
    c+=1
  return c

processes = asyncio.gather(*[f() for i in range(10000)])
res = asyncio.get_event_loop().run_until_complete(processes)
res = np.array(res)

RuntimeError: This event loop is already running

In [2]:
import asyncio
import utils
from hopfield import HopfieldNeuralNetwork
import numpy as np
import random

def background(f):
  def wrapped(*args, **kwargs):
    return asyncio.get_event_loop().run_in_executor(None, f, *args, **kwargs)
  return wrapped

weights = utils.get_adj_matrix('max_cut_data/MaxCut_50v2.mc')
print(weights.shape)

hnn = HopfieldNeuralNetwork(weights=weights, mode='ExponentialAnnealing')
n_steps = 100
n_epochs = 10000

@background
def cut(hnn, n_steps, epoch, batch_size=0.1):
  x = np.random.choice([-1, 1], size=hnn.n_neurons)
  for i, alpha in zip(range(n_steps), np.logspace(6, -5, n_steps)):
    y = hnn.predict(x, t=alpha)
    x = y
    print(f'Epoch: {epoch}, Step: {i}, Energy: {hnn.energy(y)}')
  n_cuts = np.sum(hnn.W * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y, y))) / 4
  return {'n_cuts':n_cuts, 'cut': y}

print('Hello ...')
print(await asyncio.gather(*[cut(hnn, n_steps, e) for e in range(n_epochs)]))
print('... World!')

(50, 50)
Hello ...
Epoch: 1, Step: 0, Energy: 748.5
Epoch: 0, Step: 0, Energy: 968.5Epoch: 2, Step: 0, Energy: -421.5

Epoch: 2, Step: 1, Energy: -287.5Epoch: 1, Step: 1, Energy: -495.5

Epoch: 0, Step: 1, Energy: 1230.5
Epoch: 3, Step: 0, Energy: 190.5
Epoch: 4, Step: 0, Energy: -357.5
Epoch: 5, Step: 0, Energy: 722.5
Epoch: 2, Step: 2, Energy: 98.5
Epoch: 0, Step: 2, Energy: 930.5
Epoch: 1, Step: 2, Energy: 854.5Epoch: 7, Step: 0, Energy: 1376.5

Epoch: 3, Step: 1, Energy: 810.5
Epoch: 4, Step: 1, Energy: 396.5
Epoch: 6, Step: 0, Energy: -55.5Epoch: 1, Step: 3, Energy: 464.5Epoch: 5, Step: 1, Energy: 1046.5

Epoch: 8, Step: 0, Energy: 152.5
Epoch: 0, Step: 3, Energy: 1230.5Epoch: 10, Step: 0, Energy: -621.5


Epoch: 7, Step: 1, Energy: 918.5Epoch: 9, Step: 0, Energy: 1972.5
Epoch: 4, Step: 2, Energy: 404.5

Epoch: 10, Step: 1, Energy: 674.5Epoch: 2, Step: 3, Energy: 12.5
Epoch: 1, Step: 4, Energy: 670.5
Epoch: 11, Step: 0, Energy: -659.5
Epoch: 6, Step: 1, Energy: -41.5

Epoch: 0, St

d:\Downloads\papers, books and stuff\mem-HNNs\hopfield.py:47: RuntimeWarning: overflow encountered in exp
  W_modified = np.where(self.W >= self.W_bar, alpha/(np.exp(alpha/(self.W - self.W_bar)) - 1), -alpha/(np.exp(alpha/(self.W - self.W_bar)) - 1))


Epoch: 4, Step: 3, Energy: 716.5Epoch: 10, Step: 2, Energy: -39.5

Epoch: 9, Step: 2, Energy: 2258.5
Epoch: 0, Step: 5, Energy: 1230.5Epoch: 7, Step: 3, Energy: 1360.5
Epoch: 5, Step: 3, Energy: 1046.5


Epoch: 9, Step: 3, Energy: 1686.5
Epoch: 1, Step: 6, Energy: 670.5
Epoch: 2, Step: 4, Energy: 212.5Epoch: 5, Step: 4, Energy: 992.5
Epoch: 8, Step: 2, Energy: 1234.5Epoch: 6, Step: 3, Energy: -41.5Epoch: 11, Step: 2, Energy: -51.5



Epoch: 4, Step: 4, Energy: 404.5
Epoch: 7, Step: 4, Energy: 1360.5
Epoch: 0, Step: 6, Energy: 930.5Epoch: 3, Step: 3, Energy: 854.5

Epoch: 1, Step: 7, Energy: 464.5Epoch: 2, Step: 5, Energy: 1188.5

Epoch: 4, Step: 5, Energy: 716.5Epoch: 11, Step: 3, Energy: 194.5Epoch: 10, Step: 3, Energy: 968.5
Epoch: 6, Step: 4, Energy: 200.5


Epoch: 8, Step: 3, Energy: 1392.5
Epoch: 9, Step: 4, Energy: 2258.5
Epoch: 3, Step: 4, Energy: 1052.5
Epoch: 7, Step: 5, Energy: 1360.5Epoch: 6, Step: 5, Energy: -41.5
Epoch: 10, Step: 4, Energy: 276.5

Epoch: 2, Step: 6, Energy

In [ ]:
import asyncio
import numpy as np
import pandas as pd
from hopfield import HopfieldNeuralNetwork
import utils

adjacency_matrix = utils.get_adj_matrix('max_cut_data/MaxCut_50v2.mc')
print(adjacency_matrix.shape)

hnn = HopfieldNeuralNetwork(num_neurons=len(adjacency_matrix), mode='ExponentialAnnealing')
n_epochs = 10000
n_steps = 100
energies = np.zeros((n_epochs, n_steps))

async def cut(adjacency_matrix, hnn, energies, n_steps, epoch):
  hnn.train(adjacency_matrix)
  x_pred = np.random.choice([-1, 1], size=hnn.n_neurons)
  for i, t in zip(range(n_steps), np.logspace(6, -5, n_steps)):
    y_pred = hnn.predict(x_pred, t=t)
    x_pred = y_pred
    energies[epoch][i] = np.sum(adjacency_matrix * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y_pred, y_pred))) / 4
  n_cuts = np.sum(adjacency_matrix * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y_pred, y_pred))) / 4
  return {'n_cuts':n_cuts, 'cut': y_pred}

async def wrapper(epoch):
  return await asyncio.create_task(cut(adjacency_matrix, hnn, energies, n_steps, epoch))

res = await asyncio.gather(*[wrapper(e) for e in range(n_epochs)])
res = pd.DataFrame(res)
res.loc[res['n_cuts'].idxmax()]

In [1]:
import utils

utils.generate_max_cut_instance(20, 3)

In [ ]:
import numpy as np
from hopfield import HopfieldNeuralNetwork
import utils

# Define the adjacency matrix of the graph
adjacency_matrix = utils.get_adj_matrix('max_cut_data/MaxCut_50v2.mc')
print(adjacency_matrix.shape)

energies = np.zeros((10000, 100))

# Solve the Max Cut problem
def max_cut(adjacency_matrix, num_iterations=10000):

  # Create an instance of the HopfieldNeuralNetwork with stochastic neurons
  hnn = HopfieldNeuralNetwork(num_neurons=len(adjacency_matrix), mode='ExponentialAnnealing')

  best_n_cut_edges = -1
  best_cut = None

  for epoch in range(num_iterations):
    hnn.train(adjacency_matrix)
    x_pred = np.random.choice([-1, 1], size=hnn.n_neurons)
    for it, t in zip(range(100), np.logspace(6, -5, 100)):
      y_pred = hnn.predict(x_pred, t=t)
      x_pred = y_pred
      # print(f"Iter {it}:", np.sum(adjacency_matrix * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y_pred, y_pred))) / 4)
      energies[epoch][it] = np.sum(adjacency_matrix * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y_pred, y_pred))) / 4
    
    n_cut_edges = np.sum(adjacency_matrix * (np.ones((hnn.n_neurons, hnn.n_neurons)) - np.outer(y_pred, y_pred))) / 4
    
    if n_cut_edges > best_n_cut_edges:
      best_n_cut_edges = n_cut_edges
      best_cut = y_pred
  
  return best_cut, best_n_cut_edges

# Print the best cut and the number of cut edges
best_cut, best_n_cut_edges = max_cut(adjacency_matrix)
print("Best Cut:", best_cut)
print("Number of Cut Edges:", best_n_cut_edges)

In [ ]:
import numpy as np
from neupy import algorithms

data = 
dhnet = algorithms.DiscreteHopfieldNetwork()
dhnet.train(data)

result = dhnet.predict(half_zero)
